In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
from enum import Enum
from random import random, shuffle
from __future__ import annotations
from tqdm import trange
%matplotlib osx

# Define Classes

In [2]:
class Strategy(Enum):
    PASSIVE = 0
    AGGRESSIVE = 1
    OPTIMAL = 2

In [3]:
class Agent(object):
    """
    If two Agents land on the same cell, they compete for food using their strategy.
    An Agent's survival chance is given by self.energy,
    and their reproduction chance is given by self.energy - 1.

    The only way to guarantee reproduction is to not have a competitor in that cell.
    """

    def __init__(self, strategy:Strategy) -> None:
        self.energy: float = 0.0
        self.strategy: Strategy = strategy
        self.competed: bool = False

    def will_survive(self) -> bool:
        return random() < self.energy

    def will_reproduce(self) -> bool:
        return random() < self.energy - 1

    @staticmethod
    def compete(a:Agent|None, b:Agent|None) -> bool:
        if a is None and b is None:
            return False
        if a is not None and b is None:
            a.energy = 2.0
            a.competed = False
            return True
        if b is not None and a is None:
            b.energy = 2.0
            b.competed = False
            return True
        
        if a.strategy is Strategy.PASSIVE:
            if b.strategy is Strategy.PASSIVE:
                a.energy = 1.0
                b.energy = 1.0
            else:
                a.energy = 0.5
                b.energy = 1.5
        elif a.strategy is Strategy.AGGRESSIVE:
            if b.strategy is Strategy.AGGRESSIVE:
                a.energy = 0.0
                b.energy = 0.0
            else:
                a.energy = 1.5
                b.energy = 0.5
        else:
            if b.strategy is Strategy.OPTIMAL:
                a.energy = 1.0
                b.energy = 1.0
            else:
                Agent.compete(b, a)
        a.competed = True
        b.competed = True
        return True

In [4]:
class World(object):
    """
    A World represents a list of Agents.
    """

    def __init__(
            self,
            num_agents:int=200,
            num_food:int=400,
            passive:float=0.4,
            aggressive:float=0.4
        ) -> None:

        assert passive + aggressive <= 1

        self.num_food: int = num_food

        # Create Agents
        self.agents = [Agent(Strategy.PASSIVE) for _ in range(int(passive * num_agents))]
        self.agents.extend([Agent(Strategy.AGGRESSIVE) for _ in range(int(aggressive * num_agents))])
        self.agents.extend([Agent(Strategy.OPTIMAL) for _ in range(int((1 - passive - aggressive) * num_agents))])

    def add_optimal_agents(self, proportion:float=0.0) -> None:
        """
        Based on the current total number of agents, add OPTIMAL Agents.
        """
        num_agents_to_add = int(proportion * len(self.agents))
        self.agents.extend([Agent(Strategy.OPTIMAL) for _ in range(num_agents_to_add)])

    def step(self):
        """
        Move forward one timestep. Each timestep consists of the following:

        1.  Randomly place Agents at food.
        2.  Compete for/eat food.
        3.  Decide survival for each Agent.
        4.  Decide reproduction for each surviving Agent.
        5.  Reset each Agent's energy to zero.
        """

        # 1.  Randomly place Agents at food.
        shuffle(self.agents)
        partition = int(len(self.agents) // 2)

        first_agent = [None] * self.num_food
        first_agent[:partition] = self.agents[:partition]
        shuffle(first_agent)

        second_agent = [None] * self.num_food
        second_agent[partition:len(self.agents)] = self.agents[partition:]
        shuffle(second_agent)

        # 2.  Compete for/eat food.
        singles = [0] * len(Strategy)
        pairs = [[0] * len(Strategy) for _ in Strategy]
        for i in range(self.num_food):
            first, second = first_agent[i], second_agent[i]
            if Agent.compete(first, second):
                if first is None:
                    singles[second.strategy.value] += 1
                elif second is None:
                    singles[first.strategy.value] += 1
                else:
                    pairs[first.strategy.value][second.strategy.value] += 1
                    pairs[second.strategy.value][first.strategy.value] += 1

        # 3.  Decide survival for each Agent.
        self.agents[:] = [agent for agent in self.agents if agent.will_survive()]

        # 4.  Decide reproduction for each surviving Agent.
        num_reproduce = [0] * len(Strategy)
        num_reproduce_and_competed = [0] * len(Strategy)
        for agent in self.agents:
            if agent.will_reproduce():
                self.agents.append(Agent(agent.strategy))
                num_reproduce[agent.strategy.value] += 1
                if agent.competed:
                    num_reproduce_and_competed[agent.strategy.value] += 1

        # 5.  Reset each Agent's energy to zero.
        for agent in self.agents:
            agent.energy = 0

        return singles, pairs, num_reproduce, num_reproduce_and_competed
        
    def get_num_passive(self) -> int:
        return len(list(filter(lambda agent: agent.strategy is Strategy.PASSIVE, self.agents)))

    def get_num_aggressive(self) -> int:
        return len(list(filter(lambda agent: agent.strategy is Strategy.AGGRESSIVE, self.agents)))

    def get_num_optimal(self) -> int:
        return len(list(filter(lambda agent: agent.strategy is Strategy.OPTIMAL, self.agents)))

# Create Animation

In [5]:
num_iters = 200
num_worlds = 200

writer = FFMpegWriter(fps=5)
fig, (ax1, ax2) = plt.subplots(1, 2, dpi=200, figsize=(20, 5), width_ratios=[1, 2])

worlds = [World(passive=0.5, aggressive=0.5) for _ in range(num_worlds)]

passive = [sum([world.get_num_passive() for world in worlds]) / num_worlds]
aggressive = [sum([world.get_num_aggressive() for world in worlds]) / num_worlds]
optimal = [sum([world.get_num_optimal() for world in worlds]) / num_worlds]
passive_reproduction, aggressive_reproduction, optimal_reproduction = [0], [0], [0]
passive_reproduction_and_competed, aggressive_reproduction_and_competed, optimal_reproduction_and_competed = [0], [0], [0]

with writer.saving(fig, 'pairings_and_population.mp4', dpi=200):
    for i in trange(num_iters):
        if i == 100:
            for world in worlds:
                world.add_optimal_agents(0.2)
        
        # Move one timestep
        individual_passive, individual_aggressive, individual_optimal = [], [], []
        individual_passive_reproduction, individual_aggressive_reproduction, individual_optimal_reproduction = [], [], []
        individual_passive_reproduction_and_competed, individual_aggressive_reproduction_and_competed, individual_optimal_reproduction_and_competed = [], [], []
        for world in worlds:
            singles, pairs, num_reproduce, num_reproduce_and_competed = world.step()

            # Track values
            individual_passive.append(world.get_num_passive())
            individual_aggressive.append(world.get_num_aggressive())
            individual_optimal.append(world.get_num_optimal())

            individual_passive_reproduction.append(num_reproduce[Strategy.PASSIVE.value])
            individual_aggressive_reproduction.append(num_reproduce[Strategy.AGGRESSIVE.value])
            individual_optimal_reproduction.append(num_reproduce[Strategy.OPTIMAL.value])

            individual_passive_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.PASSIVE.value])
            individual_aggressive_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.AGGRESSIVE.value])
            individual_optimal_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.OPTIMAL.value])

        passive.append(sum(individual_passive) / num_worlds)
        aggressive.append(sum(individual_aggressive) / num_worlds)
        optimal.append(sum(individual_optimal) / num_worlds)

        passive_reproduction.append(sum(individual_passive_reproduction) / num_worlds)
        aggressive_reproduction.append(sum(individual_aggressive_reproduction) / num_worlds)
        optimal_reproduction.append(sum(individual_optimal_reproduction) / num_worlds)

        passive_reproduction_and_competed.append(sum(individual_passive_reproduction_and_competed) / num_worlds)
        aggressive_reproduction_and_competed.append(sum(individual_aggressive_reproduction_and_competed) / num_worlds)
        optimal_reproduction_and_competed.append(sum(individual_optimal_reproduction_and_competed) / num_worlds)

        # Clear axes
        ax1.clear()
        ax2.clear()

        # Show pairings
        all_pairings = np.concatenate((pairs, [singles]), axis=0)
        ax1.set_title('Pairings')
        ax1.set_xticks([0, 1, 2], ['Passive', 'Aggressive', 'Optimal'])
        ax1.set_yticks([0, 1, 2, 3], ['Passive', 'Aggressive', 'Optimal', 'None'])
        ax1.imshow(all_pairings, cmap='Greys_r')

        # Population graph
        ax2.set_title('Population')
        ax2.set_xlabel('Iteration')
        ax2.set_ylabel('Number of agents')
        ax2.plot([], [], color='b', label='Passive')
        ax2.plot([], [], color='r', label='Aggressive')
        ax2.plot([], [], color='g', label='Optimal')
        ax2.stackplot(range(len(passive)), passive, aggressive, optimal, colors=['b', 'r', 'g'])
        ax2.legend()

        # Draw and save frame
        plt.draw() 
        writer.grab_frame()


100%|██████████| 200/200 [01:04<00:00,  3.12it/s]


In [6]:
writer = FFMpegWriter(fps=5)
fig, (ax1, ax2) = plt.subplots(2, 1, dpi=200, figsize=(10, 10), height_ratios=[1, 1])

with writer.saving(fig, 'reproduction.mp4', dpi=200):
    for i in range(num_iters):
        # Clear axes
        ax1.clear()
        ax2.clear()

        # Reproduction graph
        ax1.set_title('Number of Agents Who Reproduced')
        ax1.set_xlabel('Iteration')
        ax1.set_ylabel('Number of agents')
        ax1.plot([], [], color='b', label='Passive')
        ax1.plot([], [], color='r', label='Aggressive')
        ax1.plot([], [], color='g', label='Optimal')
        ax1.stackplot(range(i+2), passive_reproduction[:i+2], aggressive_reproduction[:i+2], optimal_reproduction[:i+2], colors=['b', 'r', 'g'])
        ax1.legend()

        # Reproduction and competed graph
        ax2.set_title('Number of Agents Who Competed and Reproduced')
        ax2.set_xlabel('Iteration')
        ax2.set_ylabel('Number of agents')
        ax2.plot([], [], color='b', label='Passive')
        ax2.plot([], [], color='r', label='Aggressive')
        ax2.plot([], [], color='g', label='Optimal')
        ax2.stackplot(range(i+2), passive_reproduction_and_competed[:i+2], aggressive_reproduction_and_competed[:i+2], optimal_reproduction_and_competed[:i+2], colors=['b', 'r', 'g'])
        ax2.legend()

        # Draw and save frame
        plt.draw() 
        writer.grab_frame()

# Allow Passive Agents to Reproduce

In [7]:
class Agent(object):
    """
    If two Agents land on the same cell, they compete for food using their strategy.
    An Agent's survival chance is given by self.energy,
    and their reproduction chance is given by self.energy - 1.

    The only way to guarantee reproduction is to not have a competitor in that cell.
    """

    def __init__(self, strategy:Strategy) -> None:
        self.energy: float = 0.0
        self.strategy: Strategy = strategy
        self.competed: bool = False

    def will_survive(self) -> bool:
        return random() < self.energy

    def will_reproduce(self) -> bool:
        return random() < self.energy - 1

    @staticmethod
    def compete(a:Agent|None, b:Agent|None) -> bool:
        if a is None and b is None:
            return False
        if a is not None and b is None:
            a.energy = 2.0
            a.competed = False
            return True
        if b is not None and a is None:
            b.energy = 2.0
            b.competed = False
            return True
        
        if a.strategy is Strategy.PASSIVE:
            if b.strategy is Strategy.PASSIVE:
                a.energy = 1.25
                b.energy = 1.25
            else:
                a.energy = 0.5
                b.energy = 1.5
        elif a.strategy is Strategy.AGGRESSIVE:
            if b.strategy is Strategy.AGGRESSIVE:
                a.energy = 0.0
                b.energy = 0.0
            else:
                a.energy = 1.5
                b.energy = 0.5
        else:
            if b.strategy is Strategy.OPTIMAL:
                a.energy = 1.25
                b.energy = 1.25
            else:
                Agent.compete(b, a)
        a.competed = True
        b.competed = True
        return True

In [8]:
num_iters = 200
num_worlds = 200

writer = FFMpegWriter(fps=5)
fig, (ax1, ax2) = plt.subplots(1, 2, dpi=200, figsize=(20, 5), width_ratios=[1, 2])

worlds = [World(passive=0.5, aggressive=0.5) for _ in range(num_worlds)]

passive = [sum([world.get_num_passive() for world in worlds]) / num_worlds]
aggressive = [sum([world.get_num_aggressive() for world in worlds]) / num_worlds]
optimal = [sum([world.get_num_optimal() for world in worlds]) / num_worlds]
passive_reproduction, aggressive_reproduction, optimal_reproduction = [0], [0], [0]
passive_reproduction_and_competed, aggressive_reproduction_and_competed, optimal_reproduction_and_competed = [0], [0], [0]

with writer.saving(fig, 'pairings_and_population_improve_passive.mp4', dpi=200):
    for i in trange(num_iters):
        if i == 100:
            for world in worlds:
                world.add_optimal_agents(0.2)
        
        # Move one timestep
        individual_passive, individual_aggressive, individual_optimal = [], [], []
        individual_passive_reproduction, individual_aggressive_reproduction, individual_optimal_reproduction = [], [], []
        individual_passive_reproduction_and_competed, individual_aggressive_reproduction_and_competed, individual_optimal_reproduction_and_competed = [], [], []
        for world in worlds:
            singles, pairs, num_reproduce, num_reproduce_and_competed = world.step()

            # Track values
            individual_passive.append(world.get_num_passive())
            individual_aggressive.append(world.get_num_aggressive())
            individual_optimal.append(world.get_num_optimal())

            individual_passive_reproduction.append(num_reproduce[Strategy.PASSIVE.value])
            individual_aggressive_reproduction.append(num_reproduce[Strategy.AGGRESSIVE.value])
            individual_optimal_reproduction.append(num_reproduce[Strategy.OPTIMAL.value])

            individual_passive_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.PASSIVE.value])
            individual_aggressive_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.AGGRESSIVE.value])
            individual_optimal_reproduction_and_competed.append(num_reproduce_and_competed[Strategy.OPTIMAL.value])

        passive.append(sum(individual_passive) / num_worlds)
        aggressive.append(sum(individual_aggressive) / num_worlds)
        optimal.append(sum(individual_optimal) / num_worlds)

        passive_reproduction.append(sum(individual_passive_reproduction) / num_worlds)
        aggressive_reproduction.append(sum(individual_aggressive_reproduction) / num_worlds)
        optimal_reproduction.append(sum(individual_optimal_reproduction) / num_worlds)

        passive_reproduction_and_competed.append(sum(individual_passive_reproduction_and_competed) / num_worlds)
        aggressive_reproduction_and_competed.append(sum(individual_aggressive_reproduction_and_competed) / num_worlds)
        optimal_reproduction_and_competed.append(sum(individual_optimal_reproduction_and_competed) / num_worlds)

        # Clear axes
        ax1.clear()
        ax2.clear()

        # Show pairings
        all_pairings = np.concatenate((pairs, [singles]), axis=0)
        ax1.set_title('Pairings')
        ax1.set_xticks([0, 1, 2], ['Passive', 'Aggressive', 'Optimal'])
        ax1.set_yticks([0, 1, 2, 3], ['Passive', 'Aggressive', 'Optimal', 'None'])
        ax1.imshow(all_pairings, cmap='Greys_r')

        # Population graph
        ax2.set_title('Population')
        ax2.set_xlabel('Iteration')
        ax2.set_ylabel('Number of agents')
        ax2.plot([], [], color='b', label='Passive')
        ax2.plot([], [], color='r', label='Aggressive')
        ax2.plot([], [], color='g', label='Optimal')
        ax2.stackplot(range(len(passive)), passive, aggressive, optimal, colors=['b', 'r', 'g'])
        ax2.legend()

        # Draw and save frame
        plt.draw() 
        writer.grab_frame()


100%|██████████| 200/200 [01:14<00:00,  2.70it/s]


In [9]:
writer = FFMpegWriter(fps=5)
fig, (ax1, ax2) = plt.subplots(2, 1, dpi=200, figsize=(10, 10), height_ratios=[1, 1])

with writer.saving(fig, 'reproduction_improve_passive.mp4', dpi=200):
    for i in range(num_iters):
        # Clear axes
        ax1.clear()
        ax2.clear()

        # Reproduction graph
        ax1.set_title('Number of Agents Who Reproduced')
        ax1.set_xlabel('Iteration')
        ax1.set_ylabel('Number of agents')
        ax1.plot([], [], color='b', label='Passive')
        ax1.plot([], [], color='r', label='Aggressive')
        ax1.plot([], [], color='g', label='Optimal')
        ax1.stackplot(range(i+2), passive_reproduction[:i+2], aggressive_reproduction[:i+2], optimal_reproduction[:i+2], colors=['b', 'r', 'g'])
        ax1.legend()

        # Reproduction and competed graph
        ax2.set_title('Number of Agents Who Competed and Reproduced')
        ax2.set_xlabel('Iteration')
        ax2.set_ylabel('Number of agents')
        ax2.plot([], [], color='b', label='Passive')
        ax2.plot([], [], color='r', label='Aggressive')
        ax2.plot([], [], color='g', label='Optimal')
        ax2.stackplot(range(i+2), passive_reproduction_and_competed[:i+2], aggressive_reproduction_and_competed[:i+2], optimal_reproduction_and_competed[:i+2], colors=['b', 'r', 'g'])
        ax2.legend()

        # Draw and save frame
        plt.draw() 
        writer.grab_frame()